In [2]:
import pandas as pd
import datetime
import numpy as np

import CoreTraidMath 
import CoreDraw
from tqdm import tqdm

from indicators_v2 import *

In [3]:
df_candle = pd.read_csv(r"../data/EURUSD_price_candlestick.csv")
df_candle.rename(columns={'timestamp': 'date'}, inplace=True)
df_candle

date     open    close     high      low
0      2020-09-01 03:00:00+03:00  1.19370  1.19388  1.19391  1.19368
1      2020-09-01 03:00:05+03:00  1.19387  1.19388  1.19391  1.19383
2      2020-09-01 03:00:10+03:00  1.19387  1.19384  1.19389  1.19382
3      2020-09-01 03:00:15+03:00  1.19384  1.19384  1.19386  1.19382
4      2020-09-01 03:00:20+03:00  1.19387  1.19390  1.19391  1.19383
...                          ...      ...      ...      ...      ...
99995  2020-09-06 21:52:55+03:00  1.18382  1.18382  1.18393  1.18371
99996  2020-09-06 21:53:00+03:00  1.18382  1.18382  1.18393  1.18371
99997  2020-09-06 21:53:05+03:00  1.18382  1.18382  1.18393  1.18371
99998  2020-09-06 21:53:10+03:00  1.18382  1.18382  1.18393  1.18371
99999  2020-09-06 21:53:15+03:00  1.18382  1.18382  1.18393  1.18371

[100000 rows x 5 columns]

In [4]:


class coreSignalTrande:
    
    def __init__(self, name: str, req: dict, dataType: str):
        self.name = name
        self.agrigateInds = self.createIndicatorsInstance(req)
        self.params = req['params']
        self.dataType = dataType
        
    
    def createIndicatorsInstance(self,req: dict) -> dict:
        return indicatorsAgrigator(req['indicators'])
    
    def getIndAns(self, dataDict: dict) -> dict:
        return self.agrigateInds.getAns(dataDict)
    
    def getAns(self, data: pd.DataFrame(), indDataDict: dict) -> dict:
        return self.getSigAns(data, self.getIndAns(indDataDict)) 
        
    
    
class sig_BB(coreSignalTrande):
    """
    ind keys:
        ind_BB
    """
    
    def __init__(self, name: str, req:dict):
        super().__init__(name, req, 'ochl')
    
    def getSigAns(self, data: pd.DataFrame(), indAnsDict: dict) -> dict:

        lastValue = data[self.params['source']].to_list()[-1]
        if lastValue>indAnsDict['ind_BB']['pSTD'][-1]:
            ans='down'
        elif lastValue<indAnsDict['ind_BB']['mSTD'][-1]:
            ans='up'
        else:
            ans='none'
        
        return ans
        

In [5]:
class signalsAgrigator:
    
    def __init__ (self,req:dict):
        self.signals = self.createSignalsInstance(req)
        
    def createSignalsInstance(self, siganlsDict: dict) -> dict:
        ans = {}
        for i in siganlsDict.keys():
            ans[i]=siganlsDict[i]['className'](name = i, req = siganlsDict[i])
        return ans
    
    def getAns(self, dataDict: dict) -> dict:
        ans = {}
        for i in dataDict.keys():
            ans[i] = self.signals[i].getAns(data = dataDict[i]['signalData'], 
                                   indDataDict = dataDict[i]['indicatorData'])
        return ans

In [6]:
sigreq= {
        'params':{'source':'close','target':'close'},
        'indicators':{
            'ind_BB':{
                'className':ind_BB,
                'params':{'MeanType':'SMA','window':15,'valueType':'close','kDev':2.5}
            }            
        }
    }
    
indReqDict ={'ind_BB':df_candle[:1000]}


In [7]:
sigAgrReq = {
    'sig_BB':{
        'className':sig_BB,
        'params':{'source':'close','target':'close'},
        'indicators':{
            'ind_BB':{
                'className':ind_BB,
                'params':{'MeanType':'SMA','window':15,'valueType':'close','kDev':2.5}
            }            
        }
    },
    'sig_BB_2':{
        'className':sig_BB,
        'params':{'source':'close','target':'close'},
        'indicators':{
            'ind_BB':{
                'className':ind_BB,
                'params':{'MeanType':'SMA','window':30,'valueType':'close','kDev':2}
            }            
        }
    }
}

sigAgrData = {
    'sig_BB':{
        'signalData': df_candle[990:1000],
        'indicatorData' :{'ind_BB': df_candle[:1000]}
    },
    'sig_BB_2':{
        'signalData': df_candle[990:1000],
        'indicatorData' :{'ind_BB': df_candle[:1000]}
    }    
}

In [8]:
ttt=signalsAgrigator(sigAgrReq)

In [9]:
ttt.__dict__

{'signals': {'sig_BB': <__main__.sig_BB at 0x7f1f4823e8d0>,
  'sig_BB_2': <__main__.sig_BB at 0x7f1f56191250>}}

In [10]:
ttt.signals['sig_BB'].__dict__

{'name': 'sig_BB',
 'agrigateInds': <indicators_v2.indicatorsAgrigator at 0x7f1f4a77a350>,
 'params': {'source': 'close', 'target': 'close'},
 'dataType': 'ochl'}

In [11]:
ttt.getAns(sigAgrData)

{'sig_BB': 'none', 'sig_BB_2': 'down'}

In [12]:
list({'ttt':2}.keys())[0]

'ttt'

In [13]:
test = sig_BB('sig_BB', sigreq)

In [14]:
test.__dict__

{'name': 'sig_BB',
 'agrigateInds': <indicators_v2.indicatorsAgrigator at 0x7f1f4931d750>,
 'params': {'source': 'close', 'target': 'close'},
 'dataType': 'ochl'}

In [15]:
test.agrigateInds.__dict__

{'indDict': {'ind_BB': {'className': indicators_v2.ind_BB,
   'params': {'MeanType': 'SMA',
    'window': 15,
    'valueType': 'close',
    'kDev': 2.5}}},
 'indInst': {'ind_BB': <indicators_v2.ind_BB at 0x7f1f482591d0>},
 'ans': {}}

In [16]:
ians = test.getIndAns(indReqDict)
ians

{'ind_BB': {'BB': array([1.19389133, 1.19388733, 1.193884  , 1.193884  , 1.193884  ,
         1.19388   , 1.19387733, 1.19387467, 1.193872  , 1.19387133,
         1.19387933, 1.19389   , 1.193904  , 1.193914  , 1.193922  ,
         1.19393667, 1.19395933, 1.193982  , 1.19401067, 1.19403533,
         1.194058  , 1.19408267, 1.194108  , 1.19412933, 1.19414467,
         1.19415133, 1.19415333, 1.194156  , 1.194158  , 1.19415467,
         1.19414933, 1.194144  , 1.19413933, 1.19413533, 1.19413667,
         1.19414   , 1.19414333, 1.19414733, 1.19415533, 1.19416733,
         1.194182  , 1.19419533, 1.19420667, 1.19422067, 1.19424067,
         1.19425933, 1.19427733, 1.194292  , 1.19429933, 1.19430533,
         1.19431867, 1.19432867, 1.19433533, 1.194344  , 1.19435333,
         1.194358  , 1.194364  , 1.19437067, 1.19437933, 1.194382  ,
         1.19438533, 1.19438867, 1.194392  , 1.194396  , 1.1944    ,
         1.19439667, 1.194394  , 1.19438867, 1.19438267, 1.19438   ,
         1.1943833

In [17]:
test.getAns(df_candle[:100],indReqDict)

'up'